# 🏠 Necesidad de vivienda en Villa Unión

In [1]:
# --- Librerías únicas y ordenadas ---
import sys
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import PolynomialFeatures
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score
from difflib import get_close_matches
from scipy.stats import linregress
import re
from collections import Counter

sys.path.append('../Funciones')
from funciones import  DF_CLAVES, leer_archivo, obtener_claves_estado_mun, analizar_columnas

# --- Diccionarios por año: rutas organizadas ---
rutas_diccionarios = {
    2020: "C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultados por AGEB y manzana urbana/diccionario_datos_ageb_urbana_2020.csv",
    2010: "C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultados por AGEB y manzana urbana/diccionario_ageb_urbana_cpv2010.csv",
    2005: "C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultado por ITER/diccionario_cpv2005_iter.csv",
    2000: "C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultado por ITER/diccionario_cgpv2000_iter.csv",
}

# Cargar todos los diccionarios automáticamente
diccionarios = {anio: leer_archivo(ruta) for anio, ruta in rutas_diccionarios.items()}

# --- Función robusta para consultar variable ---
def consultar_variable(diccionario_df, variable, posibles_campos_nemonico=['mnemonico', 'Mnemónico', 'Nemónico del campo'], campo_significado=2):
    """
    Consulta el significado de una variable dentro de un diccionario de datos con columnas variables.

    Parámetros:
    -----------
    diccionario_df : pd.DataFrame
        DataFrame con el diccionario de variables (por año).
    
    variable : str
        Código o mnemónico de la variable a consultar.
    
    posibles_campos_nemonico : list[str]
        Lista de posibles nombres de columnas que contienen los nemónicos.
    
    campo_significado : int o str
        Columna donde se encuentra el significado o descripción.

    Retorna:
    --------
    significado : str
        Descripción de la variable si se encuentra.
    """
    for campo in posibles_campos_nemonico:
        if campo in diccionario_df.columns:
            try:
                fila = diccionario_df[diccionario_df[campo] == variable].iloc[0]
                significado = fila.iloc[campo_significado] if isinstance(campo_significado, int) else fila[campo_significado]
                return significado
            except IndexError:
                return f"No se encontró la variable '{variable}' en el campo '{campo}'."
            except Exception as e:
                return f"Error al consultar: {e}"
    return f"No se encontró una columna de nemónicos reconocida en el diccionario."

# --- Ejemplo de uso ---
# variable = 'LOC'
# significado_2020 = consultar_variable(diccionarios[2020], variable)
# print(f"{variable} significa: {significado_2020}")
# Obtener 'CVE_ENT' y 'CVE_MUN' 

def corregir_nombres_estado_municipio(estado, municipio):
    """
    Normaliza nombres de estado y municipio usando las claves oficiales.

    Parámetros:
    ------------
    estado : str
    municipio : str

    Retorna:
    --------
    estado_normalizado, municipio_normalizado : tuple[str, str]
        Los nombres corregidos y en formato oficial según DF_CLAVES.
    
    Lanza:
    ------
    ValueError si hay errores ortográficos que no pueden corregirse.
    """
    estado = estado.strip().title()
    municipio = municipio.strip().title()

    entidades = DF_CLAVES['NOM_ENT'].unique()
    if estado not in entidades:
        sugerencia = get_close_matches(estado, entidades, n=1, cutoff=0.6)
        raise ValueError(f"Estado no encontrado. ¿Quisiste decir '{sugerencia[0]}'?" if sugerencia else f"'{estado}' no es un estado válido.")

    df_ent = DF_CLAVES[DF_CLAVES['NOM_ENT'] == estado]
    municipios = df_ent['NOM_MUN'].unique()
    if municipio not in municipios:
        sugerencia = get_close_matches(municipio, municipios, n=1, cutoff=0.6)
        raise ValueError(f"Municipio no encontrado. ¿Quisiste decir '{sugerencia[0]}'?" if sugerencia else f"'{municipio}' no está en el estado '{estado}'.")

    # Recuperar nombres corregidos (como aparecen en el archivo oficial)
    estado_corregido = df_ent['NOM_ENT'].iloc[0]
    municipio_corregido = df_ent[df_ent['NOM_MUN'] == municipio]['NOM_MUN'].iloc[0]
    return estado_corregido, municipio_corregido



**Selecionar el Estado y municipio para el estudio**

In [2]:
# Seleccionar el estado y municipio para el modelo
estado = "Sinaloa"
municipio = "mazatlán"

# Obtener 'CVE_ENT' y 'CVE_MUN' 
claves= obtener_claves_estado_mun(estado,municipio,retornar_resultado=True)

estado, municipio = corregir_nombres_estado_municipio(estado, municipio)
claves

{'CVE_ENT': np.int64(25), 'CVE_MUN': np.int64(12)}

**Extraer las bases de datos**

In [3]:

# Importar la base de datos de la población 2020 por AGEB
ruta_2020= f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultados por AGEB y manzana urbana/conjunto_de_datos_ageb_urbana_{claves['CVE_ENT']}_cpv2020.csv"
df_2020 = leer_archivo(ruta_2020)

# Importar la base de datos de la población 2010 por AGEB
ruta_2010= f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultados por AGEB y manzana urbana/resultados_ageb_urbana_{claves['CVE_ENT']}_cpv2010.csv"
df_2010 = leer_archivo(ruta_2010)

# Importar la base de datos de la población 2005 por ITER
ruta_2005= f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultado por ITER/cpv2005_iter_{claves['CVE_ENT']}.csv"
df_2005 = leer_archivo(ruta_2005)

# Importar la base de datos de la población 2000 por ITER
ruta_2000= f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultado por ITER/cgpv2000_iter_{claves['CVE_ENT']}.csv"
df_2000 = leer_archivo(ruta_2000)

# Importar la base de datos de la población 1995 por ITER
ruta_1995= f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultado por ITER/ITER_{claves['CVE_ENT']}XLS95.xls"
df_1995 = leer_archivo(ruta_1995)

# Importar la base de datos de la población 1990 por ITER
ruta_1990= f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Resultado por ITER/ITER_{claves['CVE_ENT']}XLS90.xls"
df_1990 = leer_archivo(ruta_1990)

# Importar la base de datos de la población 1980
df_1980= pd.read_excel(f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Poblacion_1980.xlsx",
                       sheet_name='CPyV80_Nal_Pob4',
                       skiprows=4 )
# Eliminar Nah
df_1980 = df_1980[df_1980['Entidad federativa'].notna()]
# Eliminar números al inicio
df_1980['Entidad federativa'] = df_1980['Entidad federativa'].str.replace(r'^\d+\s+', '', regex=True)
df_1980['Municipio'] = df_1980['Municipio'].str.replace(r'^\d+\s+', '', regex=True)

# Importar la base de datos de la población 1970
df_1970= pd.read_excel(f"C:/Users/julio/OneDrive/Documentos/Trabajo/Ideas Frescas/Bases de datos/Censo Poblacion y Vivienda/Poblacion_1970.xlsx",
                       sheet_name='CGP70_Nal_Pob3',
                       skiprows=4 )

# Filtrar por Municipio y localidad 
# Los datos de 1980 y 1970 no tiene información de localidad

# Datos Villa Unión 2020
df_villa_union_2020 = df_2020[(df_2020['NOM_MUN']==municipio) & (df_2020['LOC']==348)].iloc[0]
df_villa_union_2020 = df_villa_union_2020.to_frame().T

# Datos Villa Unión 2010
df_villa_union_2010 = df_2010[(df_2010['nom_mun']==municipio) & (df_2010['loc']==348)].iloc[0]
df_villa_union_2010 = df_villa_union_2010.to_frame().T

# Datos Villa Unión 2005
df_villa_union_2005 = df_2005[(df_2005['nom_mun']==municipio) & (df_2005['loc']==348)].iloc[0]
df_villa_union_2005 = df_villa_union_2005.to_frame().T

# Datos Villa Unión 2000
df_villa_union_2000 = df_2000[(df_2000['nom_mun']==municipio) & (df_2000['loc']==348)].iloc[0]
df_villa_union_2000 = df_villa_union_2000.to_frame().T

# Datos Villa Unión 1995
df_villa_union_1995 = df_1995[(df_1995['NOM_MUN\t']==municipio) & (df_1995['LOC\t']==348)].iloc[0]
df_villa_union_1995 = df_villa_union_1995.to_frame().T

# Datos Villa Unión 1990
df_villa_union_1990 = df_1990[(df_1990['NOM_MUN\t']==municipio) & (df_1990['LOC\t']==348)].iloc[0]
df_villa_union_1990 = df_villa_union_1990.to_frame().T

# Datos del municipio 1980
df_mun_1980 = df_1980[(df_1980['Entidad federativa']==estado) & (df_1980['Municipio'] == municipio)]

# Datos del municipio 1970
df_mun_1970 = df_1970[(df_1970['Entidad federativa']==estado) & (df_1970['Municipio'] == municipio)]

# Base de datos ampleada para analizar 2020
df_2020_completo = leer_archivo("C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Proyecto Villa Union/Base de datos/Sinaloa_2020.csv")


c:\Users\julio\OneDrive\Documentos\Trabajo\IdeasFrscas\Proyecto Villa Union\../Funciones\funciones.py:44: DtypeWarning: Columns (8) have mixed types. Specify dtype option on import or set low_memory=False.
  return pd.read_csv(ruta, encoding=enc)


**Diagnostico de la base de datos 2020**

In [4]:


def diagnostico_base_datos(df):
    print("📊 DIMENSIONES DEL DATAFRAME")
    print(df.shape)

    print("\n🧬 TIPOS DE DATOS")
    print(df.dtypes)

    print("\n🔎 PRIMEROS 5 REGISTROS")
    print(df.head())

    print("\n🧼 VALORES NULOS POR COLUMNA")
    nulos = df.isnull().sum()
    nulos = nulos[nulos > 0].sort_values(ascending=False)
    print(nulos)

    print("\n🗑️ COLUMNAS CON UN SOLO VALOR ÚNICO (POSIBLEMENTE IRRELEVANTES)")
    unicos = df.nunique()
    irrelevantes = unicos[unicos <= 1]
    print(irrelevantes)

    print("\n🧬 COLUMNAS TIPO 'object' Y SUS VALORES ÚNICOS")
    columnas_obj = df.select_dtypes(include='object').columns
    for col in columnas_obj:
        print(f"\n🧾 Columna: {col} - Valores únicos: {df[col].nunique()}")
        print(df[col].value_counts(dropna=False).head(5))

    print("\n📉 DESCRIPTIVO DE COLUMNAS NUMÉRICAS")
    print(df.describe())

    print("\n🧩 FILAS DUPLICADAS")
    duplicados = df.duplicated().sum()
    print(f"Número de filas duplicadas: {duplicados}")

    # Crear DataFrames resumen para nulos y columnas irrelevantes
    df_nulos = pd.DataFrame({'columna': nulos.index, 'valores_nulos': nulos.values})
    df_irrelevantes = pd.DataFrame({'columna': irrelevantes.index, 'valor_único': irrelevantes.values})

    # Mostrar en el entorno interactivo si estás usando Jupyter/Notebook
    try:
        import ace_tools as tools
        tools.display_dataframe_to_user(name="Resumen Nulos", dataframe=df_nulos)
        tools.display_dataframe_to_user(name="Columnas Irrelevantes", dataframe=df_irrelevantes)
    except:
        pass  # Si estás fuera de entorno con ace_tools

    return df_nulos, df_irrelevantes

# USO:
df_nulos, df_irrelevantes = diagnostico_base_datos(df_2020_completo)


📊 DIMENSIONES DEL DATAFRAME
(5552, 286)

🧬 TIPOS DE DATOS
ENTIDAD         int64
NOM_ENT        object
MUN             int64
NOM_MUN        object
LOC             int64
                ...  
VPH_SINRTV     object
VPH_SINLTC     object
VPH_SINCINT    object
VPH_SINTIC     object
TAMLOC         object
Length: 286, dtype: object

🔎 PRIMEROS 5 REGISTROS
   ENTIDAD  NOM_ENT  MUN                      NOM_MUN   LOC  \
0       25  Sinaloa    0  Total de la entidad Sinaloa     0   
1       25  Sinaloa    0  Total de la entidad Sinaloa  9998   
2       25  Sinaloa    0  Total de la entidad Sinaloa  9999   
3       25  Sinaloa    1                        Ahome     0   
4       25  Sinaloa    1                        Ahome     1   

                        NOM_LOC          LONGITUD          LATITUD ALTITUD  \
0           Total de la Entidad               NaN              NaN     NaN   
1   Localidades de una vivienda               NaN              NaN     NaN   
2  Localidades de dos viviendas     

**Limpieza de la base de datos del 2020 ampleado**

In [5]:
df_villa_union_2020_comple = df_2020_completo[(df_2020_completo['NOM_MUN']==municipio) & (df_2020_completo['LOC']==348)].copy()

# Asegurarnos de que las columnas sean numéricas, como mencionamos antes
columnas_a_convertir = df_villa_union_2020_comple.columns[8:]
df_villa_union_2020_comple[columnas_a_convertir] = df_villa_union_2020_comple[columnas_a_convertir].apply(pd.to_numeric, errors='coerce')

## Población

### Poblacion en 2020 

**Población Hombre y Mujeres Villa Unión**

In [6]:

# Obtener la población total de Villa Unión 2020
pob_fem_total = df_villa_union_2020_comple['POBFEM'].iloc[0]
pob_mas_total = df_villa_union_2020_comple['POBMAS'].iloc[0]

pob_total = pob_fem_total + pob_mas_total

# Crear DataFrame
df_genero = pd.DataFrame({
    'Sexo': ['Hombres', 'Mujeres'],
    'Población': [pob_mas_total, pob_fem_total]
})

# Crear gráfico de pastel
fig = px.pie(
    df_genero,
    names='Sexo',
    values='Población',
    title='Distribución por Sexo - Villa Unión 2020',
    color='Sexo',
    color_discrete_map={'Hombres': 'blue', 'Mujeres': 'red'},
    hole=0.4
)

# Ajustar traza de texto
fig.update_traces(
    textinfo='label+percent+value',
    textposition='inside',
    insidetextorientation='radial',
    pull=[0.05, 0.05]
)

# Añadir nota del total de la población dentro del gráfico
fig.add_annotation(
    text=f"Población total: {int(pob_total):,}",
    showarrow=False,
    font=dict(size=14),
    x=0.5,
    y=0.5,
    xanchor='center',
    yanchor='middle'
)

# Layout
fig.update_layout(
    template='plotly_white',
    font=dict(size=14),
    title_font=dict(size=18),
    annotations=[dict(
        text="Población total: {:,}".format(int(pob_total)),
        x=0.5, y=1.08, font_size=14, showarrow=False
    )]
)

fig.show()

### Población distribuida por edad

In [7]:


# Definir las edades de los grupos
edades = [
    '0-4', '5-9', '10-14','15-19','20-24',
    '25-29', '30-34', '35-39', '40-44',
    '45-49', '50-54', '55-59', '60-64',
    '65-69', '70-74', '75-79', '80-84', '85+'
]

# Crear un diccionario con los datos de población
data = {
    'Rango de edad': edades,
    'Hombres': [
        df_villa_union_2020_comple['P_0A4_M'].iloc[0],
        df_villa_union_2020_comple['P_5A9_M'].iloc[0],
        df_villa_union_2020_comple['P_10A14_M'].iloc[0],
        df_villa_union_2020_comple['P_15A19_M'].iloc[0],
        df_villa_union_2020_comple['P_20A24_M'].iloc[0],
        df_villa_union_2020_comple['P_25A29_M'].iloc[0],
        df_villa_union_2020_comple['P_30A34_M'].iloc[0],
        df_villa_union_2020_comple['P_35A39_M'].iloc[0],
        df_villa_union_2020_comple['P_40A44_M'].iloc[0],
        df_villa_union_2020_comple['P_45A49_M'].iloc[0],
        df_villa_union_2020_comple['P_50A54_M'].iloc[0],
        df_villa_union_2020_comple['P_55A59_M'].iloc[0],
        df_villa_union_2020_comple['P_60A64_M'].iloc[0],
        df_villa_union_2020_comple['P_65A69_M'].iloc[0],
        df_villa_union_2020_comple['P_70A74_M'].iloc[0],
        df_villa_union_2020_comple['P_75A79_M'].iloc[0],
        df_villa_union_2020_comple['P_80A84_M'].iloc[0],
        df_villa_union_2020_comple['P_85YMAS_M'].iloc[0]
    ],
    'Mujeres': [
        df_villa_union_2020_comple['P_0A4_F'].iloc[0],
        df_villa_union_2020_comple['P_5A9_F'].iloc[0],
        df_villa_union_2020_comple['P_10A14_F'].iloc[0],
        df_villa_union_2020_comple['P_15A19_F'].iloc[0],
        df_villa_union_2020_comple['P_20A24_F'].iloc[0],
        df_villa_union_2020_comple['P_25A29_F'].iloc[0],
        df_villa_union_2020_comple['P_30A34_F'].iloc[0],
        df_villa_union_2020_comple['P_35A39_F'].iloc[0],
        df_villa_union_2020_comple['P_40A44_F'].iloc[0],
        df_villa_union_2020_comple['P_45A49_F'].iloc[0],
        df_villa_union_2020_comple['P_50A54_F'].iloc[0],
        df_villa_union_2020_comple['P_55A59_F'].iloc[0],
        df_villa_union_2020_comple['P_60A64_F'].iloc[0],
        df_villa_union_2020_comple['P_65A69_F'].iloc[0],
        df_villa_union_2020_comple['P_70A74_F'].iloc[0],
        df_villa_union_2020_comple['P_75A79_F'].iloc[0],
        df_villa_union_2020_comple['P_80A84_F'].iloc[0],
        df_villa_union_2020_comple['P_85YMAS_F'].iloc[0]
    ]
}

# Convertir los datos en un DataFrame
df_piramide = pd.DataFrame(data)

# Total por fila
df_piramide['Total'] = df_piramide['Hombres'] + df_piramide['Mujeres']
df_piramide['% Hombres'] = (df_piramide['Hombres'] / df_piramide['Total'] * 100).round(2)
df_piramide['% Mujeres'] = (df_piramide['Mujeres'] / df_piramide['Total'] * 100).round(2)

# Total población general
pob_tot = df_piramide['Total'].sum()
df_piramide['% de Hombres totales'] = (df_piramide['Hombres'] / pob_tot * 100).round(2)
df_piramide['% de Mujeres totales'] = (df_piramide['Mujeres'] / pob_tot * 100).round(2)

# Crear gráfico
fig = go.Figure()

# Hombres
fig.add_trace(go.Bar(
    y=df_piramide['Rango de edad'],
    x=-df_piramide['Hombres'],
    name='Hombres',
    orientation='h',
    offset=-0,
    marker=dict(color='blue'),
    customdata=df_piramide[['% Hombres', '% de Hombres totales']],
    hovertemplate='Rango de edad: %{y}<br>' +
                  'Población: %{x}<br>' +
                  '% Hombres en grupo: %{customdata[0]}%<br>' +
                  '% Hombres del total: %{customdata[1]}%<extra></extra>'
))

# Mujeres
fig.add_trace(go.Bar(
    y=df_piramide['Rango de edad'],
    x=df_piramide['Mujeres'],
    name='Mujeres',
    orientation='h',
    offset=0,
    marker=dict(color='red'),
    customdata=df_piramide[['% Mujeres', '% de Mujeres totales']],
    hovertemplate='Rango de edad: %{y}<br>' +
                  'Población: %{x}<br>' +
                  '% Mujeres en grupo: %{customdata[0]}%<br>' +
                  '% Mujeres del total: %{customdata[1]}%<extra></extra>'
))

# Layout
fig.update_layout(
    title="Pirámide poblacional total de Villa Unión 2020",
    xaxis_title="Población",
    yaxis_title="Rango de Edad",
    barmode='group',
    xaxis=dict(
        showgrid=True,
        zeroline=True,
        tickvals=[-800, -600, -400, -200, 0, 200, 400, 600, 800],
        ticktext=['800', '600', '400', '200', '0', '200', '400', '600', '800'],
    ),

    height=600,
    bargap=0.1
)

fig.show()

### Migración de los residentes de Villa Union

In [8]:
# Extraer valores directamente (sin sumas)
nacidos_mismo_estado = df_villa_union_2020_comple['PNACENT'].iloc[0]
nacidos_otro_estado = df_villa_union_2020_comple['PNACOE'].iloc[0]

# Gráfico 1: Lugar de nacimiento
fig1 = go.Figure(data=[go.Pie(labels=['Nacidos en Sinaloa', 'Nacidos en otro estado'],
                              values=[nacidos_mismo_estado, nacidos_otro_estado],
                              hole=0.4)])
fig1.update_layout(title='Lugar de nacimiento de los residentes en Villa Unión (2020)')
fig1.show()

#

In [9]:
residencia_2015_mismo_estado = df_villa_union_2020_comple['PRES2015'].iloc[0]
residencia_2015_otro_estado = df_villa_union_2020_comple['PRESOE15'].iloc[0]

# Gráfico 2: Lugar de residencia en 2015 (migración reciente)
fig2 = go.Figure(data=[go.Bar(
    x=['Residían en Sinaloa en 2015', 'Residían en otro estado en 2015'],
    y=[residencia_2015_mismo_estado, residencia_2015_otro_estado],
    textposition='auto'
)])
fig2.update_layout(title='Lugar de residencia en 2015 (migración reciente)',
                   xaxis_title='Residencia en 2015',
                   yaxis_title='Personas')
fig2.show()


In [10]:
# Tabla comparativa resumen
df_comparativo = pd.DataFrame({
    'Categoría': ['Nacidos fuera de Villa Unión', 'Migraron a Villa Unión entre 2015 y 2020'],
    'Cantidad': [nacidos_otro_estado, residencia_2015_otro_estado],
    'Porcentaje sobre total analizado': [
        nacidos_otro_estado / (nacidos_mismo_estado + nacidos_otro_estado) * 100,
        residencia_2015_otro_estado / (residencia_2015_mismo_estado + residencia_2015_otro_estado) * 100
    ]
})
df_comparativo


Categoría  Cantidad  \
0              Nacidos fuera de Villa Unión      3174   
1  Migraron a Villa Unión entre 2015 y 2020      1010   

   Porcentaje sobre total analizado  
0                         18.797749  
1                          6.515288

## Proyecciones población en Villa Unión

In [11]:
# Poblacion total en la zona urbana 2020
pob_tot_2020 = df_villa_union_2020['POBTOT'].iloc[0]

# Poblacion total en la zona urbana 2010
pob_tot_2010 = df_villa_union_2010['pobtot'].iloc[0]

# Poblacion total en la zona urbana 2005
pob_tot_2005 = df_villa_union_2005['p_total'].iloc[0]

# Poblacion total en la zona urbana 2000
pob_tot_2000 = df_villa_union_2000['pobtot'].iloc[0]

# Poblacion total en la zona urbana 1995
pob_tot_1995 = df_villa_union_1995['POBTOTAL	'].iloc[0]

# Poblacion total en la zona urbana 1990
pob_tot_1990 = df_villa_union_1990['P_TOTAL	'].iloc[0]

# Poblacion total en la zona urbana 1980
#pob_tot_1980 = df_villa_union_2020['POBTOT'].iloc[0]

# Poblacion total en la zona urbana 1970
#pob_tot_1970 = df_villa_union_2020['POBTOT'].iloc[0]

# --------------------------
# Datos históricos
# --------------------------
data = {
    'Año': [2020, 2010, 2005, 2000, 1995, 1990],
    'Población Total': [
        pob_tot_2020,
        pob_tot_2010,
        pob_tot_2005,
        pob_tot_2000,
        pob_tot_1995,
        pob_tot_1990
    ]
}

df_pob = pd.DataFrame(data).sort_values('Año')

def entrenar_modelo_exponencial(años, poblacion):
    """
    Entrena un modelo de regresión exponencial: ln(poblacion) = a * año + b
    Retorna el modelo entrenado (lineal sobre log(poblacion)).
    """
    poblacion_log = np.log1p(poblacion)
    modelo = LinearRegression().fit(años, poblacion_log)
    return modelo

def entrenar_mejor_modelo_polinomial(años, poblacion, grados=[1, 2, 3, 4, 5]):
    """
    Encuentra el mejor modelo polinomial por validación cruzada (menor MSE).
    Retorna modelo, transformador de features, y el grado.
    """
    X_train, X_val, y_train, y_val = train_test_split(años, poblacion, test_size=0.2, random_state=42)
    mejor_grado, menor_error = None, float('inf')
    mejor_modelo, mejor_transformador = None, None

    for grado in grados:
        transformador = PolynomialFeatures(degree=grado)
        X_train_poly = transformador.fit_transform(X_train)
        X_val_poly = transformador.transform(X_val)

        modelo = LinearRegression().fit(X_train_poly, y_train)
        predicciones = modelo.predict(X_val_poly)

        error = mean_squared_error(y_val, predicciones)
        if error < menor_error:
            mejor_grado = grado
            menor_error = error
            mejor_modelo = modelo
            mejor_transformador = transformador

    return mejor_modelo, mejor_transformador, mejor_grado

def predecir_y_graficar_plotly(df_poblacion, anios_futuros, municipio=""):
    """
    Proyecta población usando modelos exponencial y polinomial óptimo.
    Genera gráfico interactivo y retorna predicciones.
    """
    df = df_poblacion.sort_values('Año')
    anios_hist = df['Año'].values
    poblacion_hist = df['Población Total'].values

    X = (anios_hist - 1970).reshape(-1, 1)
    y = poblacion_hist
    X_futuro = (np.array(anios_futuros) - 1970).reshape(-1, 1)

    # Modelo exponencial
    modelo_exp = entrenar_modelo_exponencial(X, y)
    y_exp = np.expm1(modelo_exp.predict(X_futuro))

    # Modelo polinomial óptimo
    modelo_poly, transformador_poly, grado_optimo = entrenar_mejor_modelo_polinomial(X, y)
    y_poly = modelo_poly.predict(transformador_poly.transform(X_futuro))

    # Crear gráfica
    fig = go.Figure()

    # Datos históricos
    fig.add_trace(go.Scatter(x=anios_hist, y=poblacion_hist, mode='lines+markers',
                             name='Histórico', marker=dict(color='blue')))

    # Proyección exponencial
    fig.add_trace(go.Scatter(x=anios_futuros, y=y_exp, mode='lines+markers',
                             name='Proyección exponencial', line=dict(dash='dot', color='green')))

    # Proyección polinomial
    fig.add_trace(go.Scatter(x=anios_futuros, y=y_poly, mode='lines+markers',
                             name=f'Proyección polinomial G{grado_optimo}', line=dict(dash='dash', color='orange')))

    # Relleno entre ambas curvas
    fig.add_trace(go.Scatter(
        x=anios_futuros + anios_futuros[::-1],
        y=y_exp.tolist() + y_poly[::-1].tolist(),
        fill='toself',
        fillcolor='rgba(0,100,80,0.2)',
        line=dict(color='rgba(255,255,255,0)'),
        hoverinfo="skip",
        showlegend=True,
        name='Rango de proyección'
    ))

    # Layout final
    fig.update_layout(
        title=f'Evolución histórica y proyecciones de población en {municipio}',
        xaxis_title='Año',
        yaxis_title='Población',
        template='plotly_white',
        hovermode='x unified',
        font=dict(size=14)
    )

    fig.show()

    return {
        "proyeccion_exponencial": y_exp,
        "proyeccion_polinomial": y_poly,
        "grado_polinomial": grado_optimo
    }

def crear_dataframe_comparativo(anios_futuros, y_exp, y_poly, grado):
    """
    Crea DataFrame comparativo entre modelos exponencial y polinomial.
    """
    df_resultado = pd.DataFrame({
        "Año": anios_futuros,
        "Exponencial": y_exp,
        f"Polinomial G{grado}": y_poly
    })

    df_resultado["Diferencia Absoluta"] = (
        df_resultado["Exponencial"] - df_resultado[f"Polinomial G{grado}"]
    ).abs().round(2)

    df_resultado["Diferencia Relativa (%)"] = (
        100 * df_resultado["Diferencia Absoluta"] / df_resultado["Exponencial"]
    ).round(1)

    return df_resultado

anios_futuros = [2025, 2030, 2035]
resultados = predecir_y_graficar_plotly(df_poblacion=df_pob, anios_futuros=anios_futuros, municipio="Mazatlán")

df_comparativo = crear_dataframe_comparativo(anios_futuros,
                                             resultados["proyeccion_exponencial"],
                                             resultados["proyeccion_polinomial"],
                                             resultados["grado_polinomial"])
df_comparativo

Año   Exponencial  Polinomial G1  Diferencia Absoluta  \
0  2025  16856.319105   17369.714286               513.40   
1  2030  17833.299286   18412.857143               579.56   
2  2035  18866.901179   19456.000000               589.10   

   Diferencia Relativa (%)  
0                      3.0  
1                      3.2  
2                      3.1

## Estimación del tipo de viviendas para el 2025 al 2030

In [12]:
# 2020
total_vivi_2020 = int(df_villa_union_2020['VIVTOT'].iloc[0])
vivhab_2020 = int(df_villa_union_2020['TVIVHAB'].iloc[0])
vivi_temp_2020 = int(df_villa_union_2020['VIVPAR_UT'].iloc[0])
vivi_desah_2020 = int(df_villa_union_2020['VIVPAR_DES'].iloc[0])

# 2010
total_vivi_2010 = int(df_villa_union_2010['vivtot'].iloc[0])
vivhab_2010 = int(df_villa_union_2010['tvivhab'].iloc[0])
vivi_temp_2010 = int(df_villa_union_2010['vivpar_ut'].iloc[0])
vivi_desah_2010 = int(df_villa_union_2010['vivpar_des'].iloc[0])

# 2005
total_vivi_2005 = int(df_villa_union_2005['t_vivhab'].iloc[0])
vivhab_2005 = int(df_villa_union_2005['vivparha'].iloc[0])

# 2000
total_vivi_2000 = int(df_villa_union_2000['totvivhab'].iloc[0])
vivhab_2000 = int(df_villa_union_2000['vivparhab'].iloc[0])

# Datos históricos de vivienda
data_viv = {
    'Año': [2020, 2010, 2005, 2000],
    'Viviendas totales': [total_vivi_2020, total_vivi_2010, total_vivi_2005, total_vivi_2000],
    'Viviendas habitadas': [vivhab_2020, vivhab_2010, vivhab_2005, vivhab_2000],
    'Viviendas deshabitadas': [vivi_desah_2020, vivi_desah_2010, 0, 0],
    'Viviendas uso temporal': [vivi_temp_2020, vivi_temp_2010, 0, 0], 
    'Viviendas sin informacion': [total_vivi_2020-vivhab_2020-vivi_desah_2020-vivi_temp_2020, total_vivi_2010-vivhab_2010-vivi_desah_2010-vivi_temp_2010, total_vivi_2005-vivhab_2005, total_vivi_2000-vivhab_2000],
}

# Crear DataFrame y asegurar orden cronológico
df_viv = pd.DataFrame(data_viv).sort_values('Año')

# Proyección de categorías individuales
def proyectar_categorias(df_categoria, anios_futuros):
    resultados = {'Año': anios_futuros}
    X = (df_categoria['Año'].values - 1970).reshape(-1, 1)
    
    for columna in df_categoria.columns[2:]:  # Omitimos 'Año' y 'Viviendas totales'
        y = df_categoria[columna].values
        mejor_grado, menor_error = None, float('inf')
        mejor_modelo, mejor_transformador = None, None

        for grado in [1, 2, 3, 4, 5]:
            transformador = PolynomialFeatures(degree=grado)
            X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)
            X_train_poly = transformador.fit_transform(X_train)
            X_val_poly = transformador.transform(X_val)

            modelo = LinearRegression().fit(X_train_poly, y_train)
            predicciones = modelo.predict(X_val_poly)
            error = mean_squared_error(y_val, predicciones)

            if error < menor_error:
                mejor_grado = grado
                menor_error = error
                mejor_modelo = modelo
                mejor_transformador = transformador

        X_futuro = (np.array(anios_futuros) - 1970).reshape(-1, 1)
        prediccion = mejor_modelo.predict(mejor_transformador.transform(X_futuro)).astype(int)
        resultados[columna] = prediccion

    # Calcular viviendas totales como suma de las categorías proyectadas
    resultados['Viviendas totales'] = (
        np.array(resultados['Viviendas habitadas']) +
        np.array(resultados['Viviendas deshabitadas']) +
        np.array(resultados['Viviendas uso temporal']) +
        np.array(resultados['Viviendas sin informacion'])
    )

    # Reorganizar columnas
    cols = ['Año', 'Viviendas totales', 'Viviendas habitadas', 'Viviendas deshabitadas', 'Viviendas uso temporal', 'Viviendas sin informacion']
    return pd.DataFrame(resultados)[cols]

# Aplicar proyección
anios_futuros = [2025, 2030, 2035]
df_proj_corrigido = proyectar_categorias(df_viv, anios_futuros)

# Concatenar histórico + proyecciones
df_viv_total = pd.concat([df_viv, df_proj_corrigido], ignore_index=True).sort_values('Año')
df_viv_total

Año  Viviendas totales  Viviendas habitadas  Viviendas deshabitadas  \
0  2000               3086                 3086                       0   
1  2005               3107                 3105                       0   
2  2010               4126                 3449                     533   
3  2020               5393                 4517                     730   
4  2025               6489                 5315                     968   
5  2030               7682                 6290                    1150   
6  2035               9052                 7440                    1333   

   Viviendas uso temporal  Viviendas sin informacion  
0                       0                          0  
1                       0                          2  
2                     144                          0  
3                     146                          0  
4                     206                          0  
5                     242                          0  
6                     279                          0

## Estimación de la densidad poblacional por vivienda

In [13]:
df_ocupacion_promedio = pd.DataFrame({
    'Año': [2020, 2010, 2005, 2000],
    'Personas viviendo en una vivienda': [
        pob_tot_2020 / vivhab_2020,
        pob_tot_2010 / vivhab_2010,
        pob_tot_2005/ vivhab_2005,
        pob_tot_2000 / vivhab_2000
    ]
})

def predecir_promedio_ocupacion(df_ocupacion, future_years, municipio=""):
    """
    Proyecta el promedio de personas por vivienda habitada con modelos polinomial y exponencial,
    detectando automáticamente si el modelo exponencial tiene sentido.
    """
    df = df_ocupacion.sort_values('Año')
    X = (df['Año'] - 1970).values.reshape(-1, 1)
    y = df['Personas viviendo en una vivienda'].values
    X_futuro = (np.array(future_years) - 1970).reshape(-1, 1)

    # Detectar tendencia (pendiente lineal)
    pendiente, _, r_value, _, _ = linregress(df['Año'], y)

    usar_exponencial = pendiente > 0 and r_value**2 > 0.6  # solo si crece y está bien ajustado

    if usar_exponencial:
        modelo_exp = entrenar_modelo_exponencial(X, y)
        pred_exp = np.exp(modelo_exp.predict(X_futuro))
    else:
        pred_exp = np.full(len(future_years), np.nan)

    modelo_poly, trans_poly, grado = entrenar_mejor_modelo_polinomial(X, y)
    pred_poly = modelo_poly.predict(trans_poly.transform(X_futuro))

    # Gráfico
    fig = go.Figure()

    # Históricos
    fig.add_trace(go.Scatter(
        x=df['Año'],
        y=df['Personas viviendo en una vivienda'],
        mode='lines+markers+text',
        name='Histórico',
        text=df['Personas viviendo en una vivienda'].round(2),
        textposition='top center'
    ))

    # Proyección polinomial
    fig.add_trace(go.Scatter(
        x=future_years,
        y=pred_poly,
        mode='lines+markers',
        name=f'Proyección Polinomial G{grado}',
        line=dict(dash='dash')
    ))

    # Proyección exponencial (solo si válida)
    if usar_exponencial:
        fig.add_trace(go.Scatter(
            x=future_years,
            y=pred_exp,
            mode='lines+markers',
            name='Proyección Exponencial',
            line=dict(dash='dot')
        ))

        # Banda de diferencia
        fig.add_trace(go.Scatter(
            x=future_years + future_years[::-1],
            y=pred_exp.tolist() + pred_poly[::-1].tolist(),
            fill='toself',
            fillcolor='rgba(0,100,80,0.2)',
            line=dict(color='rgba(255,255,255,0)'),
            hoverinfo="skip",
            showlegend=True,
            name='Rango de Proyección'
        ))

    # Layout
    fig.update_layout(
        title=f'Proyección de ocupación promedio en viviendas ({municipio})',
        xaxis_title='Año',
        yaxis_title='Personas por vivienda',
        template='plotly_white',
        hovermode='x unified'
    )

    fig.show()

    # DataFrame de salida
    df_resultado = pd.DataFrame({
        "Año": future_years,
        f"Proy. Polinomial G{grado}": np.round(pred_poly, 2)
    })

    if usar_exponencial:
        df_resultado["Proy. Exponencial"] = np.round(pred_exp, 2)
        df_resultado["Diferencia Absoluta"] = abs(df_resultado["Proy. Exponencial"] - df_resultado[f"Proy. Polinomial G{grado}"]).round(2)
        df_resultado["Diferencia Relativa (%)"] = (100 * df_resultado["Diferencia Absoluta"] / df_resultado["Proy. Exponencial"]).round(1)
    else:
        df_resultado["Proy. Exponencial"] = "No aplica"
        df_resultado["Diferencia Absoluta"] = "-"
        df_resultado["Diferencia Relativa (%)"] = "-"

    return df_resultado

future_years = [2025, 2030, 2035]

df_resultado_ocupacion = predecir_promedio_ocupacion(df_ocupacion_promedio, future_years, municipio=municipio)
df_resultado_ocupacion

Año  Proy. Polinomial G2 Proy. Exponencial Diferencia Absoluta  \
0  2025                 3.77         No aplica                   -   
1  2030                 3.85         No aplica                   -   
2  2035                 3.98         No aplica                   -   

  Diferencia Relativa (%)  
0                       -  
1                       -  
2                       -

## Calculo de Necesidad de vivienda 

In [14]:
# Crear DataFrame con población proyectada y años
df_final = pd.DataFrame({
    "Año": [2025, 2030, 2035],
    "Población proyectada": df_comparativo["Exponencial"].round(0),
    "Prom. personas por vivienda": df_resultado_ocupacion["Proy. Polinomial G2"].round(2),
    "Viviendas proyectadas totales": df_viv_total['Viviendas totales'].iloc[4:8].values,
    "Viviendas proyectadas habitadas": df_viv_total['Viviendas habitadas'].iloc[4:8].values
})

# Calcular viviendas necesarias
df_final["Viviendas necesarias (estimadas)"] = (
    df_final["Población proyectada"] / df_final["Prom. personas por vivienda"]
).round(0)

# Déficit / superávit
df_final["Déficit/Superávit total"] = (
    df_final["Viviendas proyectadas totales"] - df_final["Viviendas necesarias (estimadas)"]
).round(0)

df_final["Déficit/Superávit habitadas"] = (
    df_final["Viviendas proyectadas habitadas"] - df_final["Viviendas necesarias (estimadas)"]
).round(0)

# Reordenar columnas
df_final = df_final[
    [
        "Año",
        "Población proyectada",
        "Prom. personas por vivienda",
        "Viviendas necesarias (estimadas)",
        "Viviendas proyectadas totales",
        "Déficit/Superávit total",
        "Viviendas proyectadas habitadas",
        "Déficit/Superávit habitadas"
    ]
]

df_final


Año  Población proyectada  Prom. personas por vivienda  \
0  2025               16856.0                         3.77   
1  2030               17833.0                         3.85   
2  2035               18867.0                         3.98   

   Viviendas necesarias (estimadas)  Viviendas proyectadas totales  \
0                            4471.0                           6489   
1                            4632.0                           7682   
2                            4740.0                           9052   

   Déficit/Superávit total  Viviendas proyectadas habitadas  \
0                   2018.0                             5315   
1                   3050.0                             6290   
2                   4312.0                             7440   

   Déficit/Superávit habitadas  
0                        844.0  
1                       1658.0  
2                       2700.0

# Unidades Economicas en la Zona de Villa Unión 

In [15]:
# Ruta relativa al archivo CSV
denues_vu = "C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Proyecto Villa Union/Base de datos/INEGI_DENUE_20052025.csv"

# Se exporta la base de datos con la que se va a trabajar que se descargo de la DENUE
df_denues_vu = leer_archivo(denues_vu)

# Diccionario scian
scian = leer_archivo("C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Bases de datos/Diccionario SCIAN.xlsx") # Base de datos diccinario del SCIAN
# Diccionario de datos de la base de datos SCIAN, 
scian = scian[scian["Código"].astype(str).str.fullmatch(r"^\d{3}")] # Se filtro solo a los codigos de 3 digitos que nos indican la principal actividad economico
scian["Título"] = scian["Título"] .str.rstrip("T") # Se limpia los datos de la Columna Título
scian = scian[["Código", "Título"]] # Solo usas las siguentes columnas para hacer el filtro 
# Diccionario de Variables 
'''
Diccionario de Columnas a Utilizar 
Nombre de la Unidad Económica: Es el nombre comercial o nombre exterior con el que se identifica o anuncia la unidad económica.

Código de la clase de actividad SCIAN: El código está asignado con base en la actividad principal que desarrolla la unidad económica y de acuerdo con el Sistema de Clasificación
Industrial para América del Norte.

Descripcion estrato personal ocupado: Permite identificar el tamaño de Unidades Económicas por el número
de personal que emplean.

Tipo de vialidad: Es la superficie del terreno destinada para el tránsito vehicular y/o peatonal, en la cual se encuentra ubicada la unidad económica (calle, avenida,
andado.

Tipo de asentamiento humano: Es la clasificación que se da al asentamiento humano de acuerdo con su función (colonia, fraccionamiento, unidad habitacional, etc.).

Nombre de asentamiento humano:Es el sustantivo propio con el cual se identifica el asentamiento humano.

Tipo centro comercial: Son los caracteres alfanuméricos con los que se identifica el tipo de plaza, centro comercial, mercado.

Tipo de establecimiento: En este tipo de establecimiento están comprendidas las viviendas cuando en algún espacio de la casa-habitación, que también está destinado a
otras actividades cotidianas, se realiza alguna actividad económica.

Fecha de incorporación al DENUE: Fecha en la que la unidad económica se integró al Directorio Estadístico Nacional de Unidades Económicas.

Área geoestadística básica: Marco Geoestadístico Naciona.

Manzana: xtensión territorial que está constituida por un grupo de
viviendas, edificios, predios, lotes o terrenos de uso habitacional, comercial, industrial o de servicios.

Latitud: Es la distancia que existe entre la unidad económica y el ecuador. 

Fecha en la que la unidad económica se integró al Directorio Estadístico Nacional de Unidades Económicas.

Longitud: Es la distancia que existe entre la unidad económica y el meridiano de Greenwich.-

'''

# Lista de variables a considerar y filtrado por esas columnas 
df_denues_vu_f = df_denues_vu[[
    'Nombre de la Unidad Económica',
    'Código de la clase de actividad SCIAN',
    'Descripcion estrato personal ocupado',
    'Tipo de vialidad',
    'Tipo de asentamiento humano',
    'Nombre de asentamiento humano',
    'Tipo centro comercial',
    'Número de local',
    'Fecha de incorporación al DENUE',
    'Área geoestadística básica ',
    'Manzana',
    'Latitud', 
    'Longitud'
]]

### ----- Limpieza de datos ------ ##

# Solo se considerará el año en la Fecha de incorporación al DENU
df_denues_vu_f["Fecha de incorporación DENU"] = df_denues_vu_f['Fecha de incorporación al DENUE'].astype(str).str[:4]
# Posicionar la nueva columna en donde sea más facil leer la información 
col_f = df_denues_vu_f.pop("Fecha de incorporación DENU")
df_denues_vu_f.insert(9,"Fecha de incorporación DENU", col_f)

# Considerar solo los tres primeros digitos  del SCIAN para hacer la conección con las dos bases de datos. 
df_denues_vu_f["CLAVE SCIAN"] = df_denues_vu_f["Código de la clase de actividad SCIAN"].astype(str).str[:3]
# Se unen las dos bases de datos para obtener la principal actividad economica
df_denues_vu_f = df_denues_vu_f.merge(scian,left_on="CLAVE SCIAN", right_on="Código", how = "left")
# Se renombra la columna a utilizar
df_denues_vu_f = df_denues_vu_f.rename(columns={"Título": "Principal Actividad Economica"})
# Se eliminan las columnas que ya no son necesarias 
df_denues_vu_f = df_denues_vu_f.drop(columns=["CLAVE SCIAN","Código","Fecha de incorporación al DENUE"])
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = df_denues_vu_f.pop("Principal Actividad Economica")
df_denues_vu_f.insert(2,"Principal Actividad Economica", col_a)
df_denues_vu_f.head(3)


C:\Users\julio\AppData\Local\Temp\ipykernel_23224\2302357275.py:71: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\julio\AppData\Local\Temp\ipykernel_23224\2302357275.py:77: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Nombre de la Unidad Económica  \
0                    OFICINA DE BIENESTAR SOCIAL SSS   
1  AUPA DEL MODULO DE RIEGO NO 1 DE LA DERIVADORA...   
2          CENTRO DE ATENCION A CLIENTES VILLA UNION   

   Código de la clase de actividad SCIAN  \
0                                 114111   
1                                 221311   
2                                 221123   

                       Principal Actividad Economica  \
0                              Pesca, caza y captura   
1  Generación, transmisión, distribución y comerc...   
2  Generación, transmisión, distribución y comerc...   

  Descripcion estrato personal ocupado Tipo de vialidad  \
0                       0 a 5 personas        BOULEVARD   
1                       0 a 5 personas            CALLE   
2                       0 a 5 personas            CALLE   

  Tipo de asentamiento humano Nombre de asentamiento humano  \
0                     COLONIA                  EL TRONCONAL   
1                     COLONIA                        CENTRO   
2                      PUEBLO                   VILLA UNION   

  Tipo centro comercial Número de local Fecha de incorporación DENU  \
0                   NaN             NaN                        2020   
1                   NaN             NaN                        2010   
2                   NaN             NaN                        2014   

  Área geoestadística básica   Manzana    Latitud    Longitud  
0                        1283       13  23.188793 -106.214095  
1                        1423       17  23.189779 -106.222331  
2                        0459       13  23.187455 -106.219579

In [16]:
# Graficar el número de comercios con la funcion creada grafica interactiva 
concentrado_denue = analizar_columnas(df_denues_vu_f,"Principal Actividad Economica",100)
# Crear el CSV de la base de datos filtrados 
concentrado_denue.to_csv(f"Total de SCIAN en Villa Union.csv", index=False, encoding='ISO-8859-1')
concentrado_denue.head(6)

Estos son los datos que representan el 100% de los valores. De la columna Principal Actividad Economica


Principal Actividad Economica  Cantidad
0  Comercio al por menor de abarrotes, alimentos,...       206
1    Servicios de preparación de alimentos y bebidas       138
2            Servicios de reparación y mantenimiento       100
3                               Servicios personales        54
4  Comercio al por menor de productos textiles, b...        46
5                              Industria alimentaria        41

## **Analizaremos a total del municipio de Mazatlán**



In [17]:
# Datos todo el Municipio de Mazatlán 2020
df_2020_completo = leer_archivo("C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Proyecto Villa Union/Base de datos/Sinaloa_2020.csv")
df_mun_tot = df_2020_completo[df_2020_completo['NOM_MUN']==municipio]

# Datos todo el Municipio de Mazatlán 2010
df_2010_completo = leer_archivo("C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Proyecto Villa Union/Base de datos/Sinaloa_2010.csv")
df_mun_tot_2010 = df_2010_completo[df_2010_completo['nom_mun']==municipio]

# Datos todo el Municipio de Mazatlán 2005
df_2005_completo = leer_archivo("C:/Users/julio/OneDrive/Documentos/Trabajo/IdeasFrscas/Proyecto Villa Union/Base de datos/Sinaloa_2005.csv")
df_mun_tot_2005 = df_2005_completo[df_2005_completo['nom_mun']==municipio]


## ----- Limpieza de datos ------ ##
# ----- Analizar carecteres raros dentro de la base de datos 2020 ------- #

# Selecciona las columnas numericas a partir de la columna 7 para hacer el analisis
sub_df = df_mun_tot.iloc[:, 9:].astype(str)

# Inicializa una lista para almacenar caracteres raros
caracteres_raros = []

# Recorre cada columna y cada valor
for col in sub_df.columns:
    for valor in sub_df[col]:
        encontrados = re.findall(r'[^0-9\.\-]', valor)  # Excluye dígitos, punto y guion
        caracteres_raros.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres = Counter(caracteres_raros)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres.keys()))
#print("Frecuencias:", conteo_caracteres)


# ----- Analizar carecteres raros dentro de la base de datos 2010 ------- #

# Selecciona las columnas numericas a partir de la columna 7 para hacer el analisis
sub_df_2010 = df_mun_tot_2010.iloc[:, 9:].astype(str)

# Inicializa una lista para almacenar caracteres raros
caracteres_raros_2010 = []

# Recorre cada columna y cada valor
for col in sub_df_2010.columns:
    for valor in sub_df_2010[col]:
        encontrados = re.findall(r'[^0-9\.\-]', valor)  # Excluye dígitos, punto y guion
        caracteres_raros_2010.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres_2010 = Counter(caracteres_raros_2010)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres_2010.keys()))
#print("Frecuencias:", conteo_caracteres_2010)

# ----- Analizar carecteres raros dentro de la base de datos 2005 ------- #

# Selecciona las columnas numericas a partir de la columna 7 para hacer el analisis
sub_df_2005 = df_mun_tot_2005.iloc[:, 9:].astype(str)

# Inicializa una lista para almacenar caracteres raros
caracteres_raros_2005 = []

# Recorre cada columna y cada valor
for col in sub_df_2005.columns:
    for valor in sub_df_2005[col]:
        encontrados = re.findall(r'[^0-9\.\-]', valor)  # Excluye dígitos, punto y guion
        caracteres_raros_2005.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres_2005 = Counter(caracteres_raros_2005)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres_2005.keys()))
#print("Frecuencias:", conteo_caracteres_2005)


# ----- Limpieza de datos 2020 ------- #

# Lista para coordenadas sospechosas
coordenadas_con_caracteres = []

def limpiar_columna(col):
    col_str = col.astype(str).str.strip()
    
    # Casos que deben ser convertidos a '0'
    solo_raros = col_str.isin(list(conteo_caracteres.keys())) | col.isna()
    
    # Casos con mezcla (no limpiar, solo registrar)
    contiene_raros = col_str.str.contains(r'[^0-9\.\-]', regex=True) & ~solo_raros

    # Reemplazo directo
    col_str[solo_raros] = '0'
    
    # Registro de coordenadas sospechosas
    coordenadas_con_caracteres.extend(zip(contiene_raros[contiene_raros].index, [col.name]*contiene_raros.sum()))
    
    return pd.to_numeric(col_str, errors='coerce')

# Aplicar a todas las columnas relevantes
sub_df = sub_df.apply(limpiar_columna)
sub_df = sub_df.apply(pd.to_numeric, errors='coerce')

# Actualizar el DataFrame original
df_mun_tot.iloc[:, 9:] = sub_df

# Mostrar coordenadas de valores sospechosos
df_coords = pd.DataFrame(coordenadas_con_caracteres, columns=['Fila', 'Columna'])
#df_coords

# ----- Limpieza de datos 2010 ------- #

# Lista para coordenadas sospechosas
coordenadas_con_caracteres_2010 = []

def limpiar_columna(col):
    col_str = col.astype(str).str.strip()
    
    # Casos que deben ser convertidos a '0'
    solo_raros = col_str.isin(list(conteo_caracteres_2010.keys())) | col.isna()
    
    # Casos con mezcla (no limpiar, solo registrar)
    contiene_raros = col_str.str.contains(r'[^0-9\.\-]', regex=True) & ~solo_raros

    # Reemplazo directo
    col_str[solo_raros] = '0'
    
    # Registro de coordenadas sospechosas
    coordenadas_con_caracteres_2010.extend(zip(contiene_raros[contiene_raros].index, [col.name]*contiene_raros.sum()))
    
    return pd.to_numeric(col_str, errors='coerce')

# Aplicar a todas las columnas relevantes
sub_df_2010 = sub_df_2010.apply(limpiar_columna)
sub_df_2010 = sub_df_2010.apply(pd.to_numeric, errors='coerce')

# Actualizar el DataFrame original
df_mun_tot_2010.iloc[:, 9:] = sub_df_2010

# Mostrar coordenadas de valores sospechosos
df_coords_2010 = pd.DataFrame(coordenadas_con_caracteres_2010, columns=['Fila', 'Columna'])
#filas_objetivo = [3810, 4179, 4180]
#f_mun_tot_2010.loc[filas_objetivo, 'tam_loc'] = df_mun_tot_2010.loc[filas_objetivo, 'tam_loc'].fillna(0)

# ----- Limpieza de datos 2005 ------- #

# Lista para coordenadas sospechosas
coordenadas_con_caracteres_2005 = []

def limpiar_columna(col):
    col_str = col.astype(str).str.strip()
    
    # Casos que deben ser convertidos a '0'
    solo_raros = col_str.isin(list(conteo_caracteres_2005.keys())) | col.isna()
    
    # Casos con mezcla (no limpiar, solo registrar)
    contiene_raros = col_str.str.contains(r'[^0-9\.\-]', regex=True) & ~solo_raros

    # Reemplazo directo
    col_str[solo_raros] = '0'
    
    # Registro de coordenadas sospechosas
    coordenadas_con_caracteres_2005.extend(zip(contiene_raros[contiene_raros].index, [col.name]*contiene_raros.sum()))
    
    return pd.to_numeric(col_str, errors='coerce')

# Aplicar a todas las columnas relevantes
sub_df_2005 = sub_df_2005.apply(limpiar_columna)
sub_df_2005 = sub_df_2005.apply(pd.to_numeric, errors='coerce')

# Actualizar el DataFrame original
df_mun_tot_2005.iloc[:, 9:] = sub_df_2005

# Mostrar coordenadas de valores sospechosos
#df_coords = pd.DataFrame(coordenadas_con_caracteres_2005, columns=['Fila', 'Columna'])
#df_coords


# ------ Corroboramos que este bien 2020 ------- #

sub_df = df_mun_tot.iloc[:, 9:].copy()
# Inicializa una lista para almacenar caracteres raros
caracteres_raros = []

# Recorre cada columna y cada valor
for col in sub_df.columns:
    for valor in sub_df[col]:
        encontrados = re.findall(r'[^0-9\.\-]', str(valor))  # Excluye dígitos, punto y guion
        caracteres_raros.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres = Counter(caracteres_raros)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres.keys()))
#print("Frecuencias:", conteo_caracteres)

# ------ Corroboramos que este bien 2010 ------- #

sub_df = df_mun_tot_2010.iloc[:, 9:].copy()
# Inicializa una lista para almacenar caracteres raros
caracteres_raros = []

# Recorre cada columna y cada valor
for col in sub_df.columns:
    for valor in sub_df[col]:
        encontrados = re.findall(r'[^0-9\.\-]', str(valor))  # Excluye dígitos, punto y guion
        caracteres_raros.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres = Counter(caracteres_raros)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres.keys()))
#print("Frecuencias:", conteo_caracteres)

# ------ Corroboramos que este bien 2005 ------- #

sub_df = df_mun_tot_2005.iloc[:, 9:].copy()
# Inicializa una lista para almacenar caracteres raros
caracteres_raros_2005 = []

# Recorre cada columna y cada valor
for col in sub_df.columns:
    for valor in sub_df[col]:
        encontrados = re.findall(r'[^0-9\.\-]', str(valor))  # Excluye dígitos, punto y guion
        caracteres_raros_2005.extend(encontrados)

# Contar ocurrencias totales
conteo_caracteres_2005 = Counter(caracteres_raros_2005)

# Mostrar resultados
#print("Caracteres no numéricos encontrados en todo el DataFrame:", list(conteo_caracteres_2005.keys()))
#print("Frecuencias:", conteo_caracteres_2005)

c:\Users\julio\OneDrive\Documentos\Trabajo\IdeasFrscas\Proyecto Villa Union\../Funciones\funciones.py:44: DtypeWarning:

Columns (8) have mixed types. Specify dtype option on import or set low_memory=False.



**Agrupar por localicades de interes**

In [18]:
# BASE DE DATOS 2020
lista_valores_eliminar_2020 = ['Total del Municipio','Total AGEB urbana', 'Total de la localidad urbana', 'Total del municipio','Localidades de una vivienda','Localidades de dos viviendas']
def dms_a_decimal(coord):
    import re

    # Validar entrada
    if pd.isna(coord):
        return None

    coord = str(coord).strip()

    # Buscar grados, minutos, segundos y dirección
    match = re.match(r"(\d+)°(\d+)'([\d\.]+)\"?\s*([NSEW])", coord)
    if not match:
        return None  # formato inválido

    grados, minutos, segundos, direccion = match.groups()
    decimal = float(grados) + float(minutos)/60 + float(segundos)/3600

    if direccion in ['S', 'W']:
        decimal *= -1

    return decimal

df_mun_tot['LAT_DECIMAL'] = df_mun_tot['LATITUD'].apply(dms_a_decimal)
df_mun_tot['LON_DECIMAL'] = df_mun_tot['LONGITUD'].apply(dms_a_decimal)

df_filtrado_2020 = df_mun_tot[~df_mun_tot['NOM_LOC'].isin(lista_valores_eliminar_2020)]
columnas_a_sumar_2020 = df_filtrado_2020.columns[9:]  # columnas desde la 7 en adelante
df_agrupado_2020 = df_filtrado_2020.groupby('NOM_LOC')[columnas_a_sumar_2020].sum().reset_index()
df_agrupado_2020 = df_agrupado_2020.sort_values(by='POBTOT', ascending=False)
df_agrupado_2020.head(10)

C:\Users\julio\AppData\Local\Temp\ipykernel_23224\1764550628.py:25: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\julio\AppData\Local\Temp\ipykernel_23224\1764550628.py:26: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



NOM_LOC  POBTOT  POBFEM  POBMAS  P_0A2 P_0A2_F  \
270                     Mazatlán  441975  227109  214866  18254    9033   
350                  Villa Unión   16934    8502    8432    800     386   
133  Fraccionamiento los Ángeles    9140    4667    4473    599     284   
121                    El Walamo    3550    1719    1831    141      63   
40                   El Castillo    2613    1305    1308    149      87   
104                     El Roble    2314    1165    1149     66      33   
4                         Barrón    1994     958    1036     86      44   
97                    El Quelite    1455     717     738     74      35   
6                         CERESO    1223       0       0      0       0   
62                      El Habal    1146     600     546     51      30   

    P_0A2_M P_3YMAS P_3YMAS_F P_3YMAS_M  ... VPH_STVP VPH_SPMVPI VPH_CVJ  \
270    9221  423609    218021    205588  ...    66673      38983   21375   
350     414   16126      8111      8015  ...     2342        523     309   
133     315    8541      4383      4158  ...     1270        203     182   
121      78    3409      1656      1753  ...      371         53      32   
40       62    2464      1218      1246  ...      233         78      59   
104      33    2248      1132      1116  ...      517         92      58   
4        42    1908       914       994  ...      191         18      13   
97       39    1381       682       699  ...      300          9      11   
6         0       0         0         0  ...        0          0       0   
62       21    1095       570       525  ...      160         24      22   

    VPH_SINRTV VPH_SINLTC VPH_SINCINT VPH_SINTIC TAMLOC LAT_DECIMAL  \
270       3341       4833       37803        869     12   23.200316   
350        254        333        2072         75      8   23.188643   
133        163        170        1382         35      6   23.186923   
121         51         90         588         13      5   23.141124   
40          31         53         331         18      5   23.194700   
104         28         64         377         15      4   23.245023   
4           30         72         431          8      4   23.123616   
97          23         49         349          8      4   23.557692   
6            0          0           0          0      4   23.198380   
62          13         33         198          6      4   23.351239   

    LON_DECIMAL  
270 -106.422221  
350 -106.219964  
133 -106.330386  
121 -106.245649  
40  -106.339484  
104 -106.205812  
4   -106.276232  
97  -106.468816  
6   -106.316497  
62  -106.417367  

[10 rows x 280 columns]

**1. Detección de localidades con mayor déficit de servicios básicos**

Se identifican las localidades con mayor carencia en servicios elementales mediante el análisis de las siguientes columnas:

- **`VPH_S_ELEC`**: Viviendas particulares habitadas **sin energía eléctrica**  
- **`VPH_AGUAFV`**: Viviendas particulares habitadas **sin agua entubada** dentro de la vivienda  
- **`VPH_NODREN`**: Viviendas particulares habitadas **sin drenaje**  
- **`VPH_NDEAED`**: Viviendas particulares habitadas **sin energía eléctrica, agua entubada ni drenaje**
**🔍 Insight potencial:**

Las localidades con una **alta proporción de viviendas sin acceso a servicios básicos** representan zonas prioritarias para el desarrollo de **proyectos de vivienda social o progresiva**.


In [19]:
from geopy.distance import geodesic

# Coordenadas de Villa Unión (desde el DataFrame original que sí tiene coordenadas)
coord_villa_union = (
    df_mun_tot[df_mun_tot['NOM_LOC'] == 'Villa Unión']['LAT_DECIMAL'].values[0],
    df_mun_tot[df_mun_tot['NOM_LOC'] == 'Villa Unión']['LON_DECIMAL'].values[0]
)

# Copiar solo lo necesario
df_deficit_serv = df_agrupado_2020[["NOM_LOC", "VIVTOT", "VIVPAR_HAB","VIVPAR_DES","VIVPAR_UT","VPH_S_ELEC", "VPH_AGUAFV", "VPH_NODREN",'VPH_NDEAED']].copy()

# Calcular porcentaje promedio de viviendas sin servicios básicos
df_deficit_serv["% sin servicios electricidad"] = df_deficit_serv["VPH_S_ELEC"] / df_deficit_serv["VIVTOT"] * 100
df_deficit_serv["% sin servicios agua"] = df_deficit_serv["VPH_AGUAFV"] / df_deficit_serv["VIVTOT"] * 100
df_deficit_serv["% sin servicios drenaje"] = df_deficit_serv["VPH_NODREN"] / df_deficit_serv["VIVTOT"] * 100
df_deficit_serv["% sin ningun servicios"] = df_deficit_serv["VPH_NDEAED"] / df_deficit_serv["VIVTOT"] * 100
df_deficit_serv["% sin servicios"] = (
    df_deficit_serv["% sin servicios electricidad"] +
    df_deficit_serv["% sin servicios agua"] +
    df_deficit_serv["% sin servicios drenaje"] + df_deficit_serv["% sin ningun servicios"]
) / 4
# ------ Basado en el % de viviendas sin servicios calculamos las viviendas necesarios de calidad de vida ------ #

df_deficit_serv["Viviendas dignas necesarias"] =  (
    df_deficit_serv["VPH_S_ELEC"] +
    df_deficit_serv["VPH_AGUAFV"] +
    df_deficit_serv["VPH_NODREN"] + 
    df_deficit_serv["VPH_NDEAED"]
    )

# Agregar coordenadas desde df_mun_tot
df_coords = df_mun_tot[["NOM_LOC", "LAT_DECIMAL", "LON_DECIMAL"]].drop_duplicates()
df_deficit_serv = df_deficit_serv.merge(df_coords, on="NOM_LOC", how="left")

# Eliminar filas sin coordenadas
df_deficit_serv = df_deficit_serv.dropna(subset=['LAT_DECIMAL', 'LON_DECIMAL'])

# Calcular distancia a Villa Unión
df_deficit_serv['Distancia a Villa Unión (km)'] = df_deficit_serv.apply(
    lambda row: geodesic(coord_villa_union, (row['LAT_DECIMAL'], row['LON_DECIMAL'])).km, axis=1
)

# Filtrar localidades distintas a Villa Unión
#df_filtrado = df_deficit_serv[df_deficit_serv['NOM_LOC'] != 'Villa Unión']

# Filtrar localidades a 25 km o menos de Villa Unión
df_cercanas_deficit = df_deficit_serv[df_deficit_serv['Distancia a Villa Unión (km)'] <= 25] \
    .sort_values(by='% sin servicios',ascending=False)


df_cercanas_deficit = df_cercanas_deficit[df_cercanas_deficit["% sin servicios"] > 0].copy()
total_viv_nec = df_cercanas_deficit["Viviendas dignas necesarias"].sum()
print(f"Total de viviendas dignas necesarias en localidades cercanas a Villa Unión y Villa Unión: {total_viv_nec}")
df_cercanas_deficit.to_csv("Viviendas necesarias en localidades cercanas a Villa Unión.csv", index=False, encoding='ISO-8859-1')

Total de viviendas dignas necesarias en localidades cercanas a Villa Unión y Villa Unión: 2629


🧒 2. Localidades con alta proporción de población infantil
Las viviendas sociales suelen priorizar zonas con alta población dependiente.

Columnas clave:

P_0A4, P_5A9, P_10A14, P_15A19

In [20]:
df_agrupado_2020["POB_0A19"] = (
    df_agrupado_2020["P_0A4"] +
    df_agrupado_2020["P_5A9"] +
    df_agrupado_2020["P_10A14"] +
    df_agrupado_2020["P_15A19"]
)

df_agrupado_2020["%_menores"] = (df_agrupado_2020["POB_0A19"] / df_agrupado_2020["POBTOT"]) * 100
df_agrupado_2020.sort_values("%_menores", ascending=False).head(5)


NOM_LOC  POBTOT POBFEM POBMAS P_0A2 P_0A2_F  \
202  Las Garrapatas [Granja Avícola]      12      6      6     0       0   
127       Escamilla [Granja Avícola]      21      9     12     2       1   
155   La Escondida [Granja Agrícola]      13      6      7     0       0   
29                      El Austracal      23     10     13     1       1   
272                          Metates      43     25     18     5       3   

    P_0A2_M P_3YMAS P_3YMAS_F P_3YMAS_M  ... VPH_CVJ VPH_SINRTV VPH_SINLTC  \
202       0      12         6         6  ...       0          0          0   
127       1      19         8        11  ...       0          0          0   
155       0      13         6         7  ...       0          0          0   
29        0      22         9        13  ...       0          1          0   
272       2      38        22        16  ...       0          2          3   

    VPH_SINCINT VPH_SINTIC TAMLOC LAT_DECIMAL LON_DECIMAL POB_0A19  %_menores  
202           3          0      1   23.221171 -106.168625        7  58.333333  
127           4          0      1   23.280462 -106.250539       12  57.142857  
155           3          0      1   23.219778 -106.176643        7  53.846154  
29            5          0      1   23.466553 -106.459499       12  52.173913  
272           9          1      1   23.785108 -106.025061       22  51.162791  

[5 rows x 282 columns]

💼 3. Relación entre empleo e informalidad
Buscar localidades con baja ocupación (POCUPADA) y alta población sin afiliación a salud (PSINDER) puede sugerir necesidad de vivienda subsidiada.

In [21]:
df_agrupado_2020["% sin afiliación salud"] = (df_agrupado_2020["PSINDER"] / df_agrupado_2020["POBTOT"]) * 100
df_agrupado_2020["% ocupada"] = (df_agrupado_2020["POCUPADA"] / df_agrupado_2020["PEA"]) * 100
df_agrupado_2020[["NOM_LOC", "% ocupada", "% sin afiliación salud"]].sort_values("% sin afiliación salud", ascending=False).head(10)


ZeroDivisionError: division by zero

🧓 5. Localidades con jefatura femenina
Columnas: HOGJEF_F, HOGJEF_M

Una mayor jefatura femenina suele correlacionarse con vulnerabilidad social en México.

In [ ]:
df_agrupado_2020["% jefatura femenina"] = (df_agrupado_2020["HOGJEF_F"] / df_agrupado_2020["TOTHOG"]) * 100
df_agrupado_2020.sort_values("% jefatura femenina", ascending=False)[["NOM_LOC", "% jefatura femenina"]].head(10)


📈 6. Construcción de un Índice de Vulnerabilidad Habitacional (IVH)
Puedes crear un índice sintético sumando variables estandarizadas (z-scores) para:

% sin servicios básicos

Hacinamiento

% sin afiliación a salud

% de menores de edad

% de jefatura femenina  



🧮 Paso 1: Construcción del IVH
Agruparemos los siguientes componentes (todos por localidad):

Componente	Variable del DataFrame	Interpretación
A) % de viviendas sin servicios	VPH_DEF_SERV / VIVTOT	Falta de luz, agua o drenaje
B) Hacinamiento	PRO_OCUP_C	Personas por cuarto
C) % sin afiliación a salud	PSINDER / POBTOT	Vulnerabilidad económica
D) % menores de edad	POB_0A19 / POBTOT	Alta dependencia
E) % jefatura femenina	HOGJEF_F / TOTHOG	Mayor riesgo de exclusión

In [ ]:
from scipy.stats import zscore

# A) % sin servicios básicos
df_agrupado_2020["%_sin_servicios"] = (
    df_agrupado_2020["VPH_S_ELEC"] +
    df_agrupado_2020["VPH_AGUAFV"] +
    df_agrupado_2020["VPH_NODREN"]
) / df_agrupado_2020["VIVTOT"]

# B) Hacinamiento ya está como PRO_OCUP_C

# C) % sin afiliación a salud
df_agrupado_2020["%_sin_salud"] = df_agrupado_2020["PSINDER"] / df_agrupado_2020["POBTOT"]

# D) % menores de edad (0 a 19 años)
df_agrupado_2020["POB_0A19"] = (
    df_agrupado_2020["P_0A4"] + df_agrupado_2020["P_5A9"] +
    df_agrupado_2020["P_10A14"] + df_agrupado_2020["P_15A19"]
)
df_agrupado_2020["%_menores"] = df_agrupado_2020["POB_0A19"] / df_agrupado_2020["POBTOT"]

# E) % jefatura femenina
df_agrupado_2020["%_jefa_fem"] = df_agrupado_2020["HOGJEF_F"] / df_agrupado_2020["TOTHOG"]


🔢 Paso 2: Normalizar y sumar z-scores

In [ ]:
# Normalizar variables
componentes = [
    "%_sin_servicios", "PRO_OCUP_C", "%_sin_salud", "%_menores", "%_jefa_fem"
]

for comp in componentes:
    df_agrupado_2020[f"z_{comp}"] = zscore(df_agrupado_2020[comp].fillna(0))

# IVH: Índice de Vulnerabilidad Habitacional
df_agrupado_2020["IVH"] = df_agrupado_2020[[f"z_{c}" for c in componentes]].sum(axis=1)


In [ ]:
import plotly.express as px
import pandas as pd

# Suponemos que el DataFrame df_agrupado_2020 ya contiene las columnas necesarias
# Para este ejemplo, vamos a simular un DataFrame de ejemplo con los campos clave

# Simulación de un subconjunto de ejemplo si fuera necesario
# En la implementación real, esto vendría del df_agrupado_2020 del usuario
# Aquí solo estamos generando un ejemplo sintético en caso de que no haya datos cargados
example_data = {
    "NOM_LOC": [f"Localidad {i}" for i in range(1, 11)],
    "IVH": [2.3, 1.8, 3.1, 2.9, 1.5, 3.7, 2.6, 3.0, 1.9, 2.8],
}
df_ivh_top10 = pd.DataFrame(example_data).sort_values(by="IVH", ascending=False)

# Gráfico de barras interactivo
fig = px.bar(
    df_ivh_top10,
    x="IVH",
    y="NOM_LOC",
    orientation="h",
    title="Top 10 Localidades con Mayor Índice de Vulnerabilidad Habitacional (IVH)",
    labels={"IVH": "Índice de Vulnerabilidad Habitacional", "NOM_LOC": "Localidad"},
)

fig.update_layout(yaxis=dict(autorange="reversed"))

import ace_tools as tools; tools.display_dataframe_to_user(name="Top 10 IVH", dataframe=df_ivh_top10)

fig.show()


In [ ]:
# BASE DE DATOS 2010
lista_valores_eliminar_2010 = ['Total del Municipio','Total AGEB urbana', 'Total de la localidad urbana', 'Total del municipio']

df_filtrado_2010 = df_mun_tot_2010[~df_mun_tot_2010['nom_loc'].isin(lista_valores_eliminar_2010)]
columnas_a_sumar_2010 = df_filtrado_2010.columns[9:]  # columnas desde la 7 en adelante
df_agrupado_2010 = df_filtrado_2010.groupby('nom_loc')[columnas_a_sumar_2010].sum().reset_index()
df_agrupado_2010 = df_agrupado_2010.sort_values(by='pobtot', ascending=False)
df_agrupado_2010.head(10)


In [ ]:
# BASE DE DATOS 2005
lista_valores_eliminar_2005 = ['Total del Municipio','Total AGEB urbana', 'Total de la localidad urbana', 'Total del municipio']

df_filtrado_2005 = df_mun_tot_2005[~df_mun_tot_2005['nom_loc'].isin(lista_valores_eliminar_2005)]
columnas_a_sumar_2005 = df_filtrado_2005.columns[9:]  # columnas desde la 7 en adelante
df_agrupado_2005 = df_filtrado_2005.groupby('nom_loc')[columnas_a_sumar_2005].sum().reset_index()
df_agrupado_2005 = df_agrupado_2005.sort_values(by='p_total', ascending=False)
df_agrupado_2005.head(10)